In [2]:
import os
import pandas as pd
#import numpy as np
#import matplotlib.pyplot as plt
#import seaborn as sns
import geopandas
import folium
import branca.colormap as colormap

In [4]:
### Load data from filenames
#parent_folder = os.getcwd() + '/'
parent_folder = '/Users/Karen/OneDrive/GitHub/ctc21-doric-tiles/'
code_folder = parent_folder + 'code/'
data_folder =  parent_folder + 'data/'

### Datasets
places = pd.read_csv(data_folder + 'placenames_updated.csv')
parish_area = geopandas.read_file(data_folder + 'CivilParish1930_epsg4326.shp')

In [53]:
places['map_loc'] = places.apply(lambda x: x['coords'] \
                                            .split(')')[0].split('(')[1] \
                                            .replace('(','').replace(')','') \
                                            .split(' ')
                                        , axis=1
)
places['map_loc_latlong'] = places.apply(lambda x: str(
                                                        x['map_loc'][1] 
                                                        +' '+ 
                                                        x['map_loc'][0]
                                                        )
                                                    ,axis=1)

places.head(5)


place      place_EN  place_SCO  \
0   http://www.wikidata.org/entity/Q1017022   Aberchirder  Fogieloan   
1    http://www.wikidata.org/entity/Q323196        Aboyne      Abyne   
2  http://www.wikidata.org/entity/Q64947604    Aikenshill        NaN   
3   http://www.wikidata.org/entity/Q2638187        Alford     Aaford   
4   http://www.wikidata.org/entity/Q4731066  Allanaquoich        NaN   

                       coords                 map_loc      map_loc_latlong  
0     Point(-2.63004 57.5583)     [-2.63004, 57.5583]     57.5583 -2.63004  
1     Point(-2.77949 57.0766)     [-2.77949, 57.0766]     57.0766 -2.77949  
2  Point(-2.054092 57.288207)  [-2.054092, 57.288207]  57.288207 -2.054092  
3          Point(-2.71 57.23)          [-2.71, 57.23]          57.23 -2.71  
4           Point(-3.45 57.0)           [-3.45, 57.0]           57.0 -3.45

In [5]:
### Temp filter to help loadtime
parish_area = parish_area[parish_area['name'].str.startswith('A')]

print(parish_area.head(5))

      SHAPE_Leng    SHAPE_Area code C91code1 C91code2 C91code3 C91code4  \
4   41368.342275  2.932819e+07  019    05001     None     None     None   
11  58854.490736  1.135828e+08  008    07001     None     None     None   
16  39542.312713  3.620057e+07  016    51002     None     None     None   
27  30126.559506  3.092536e+07  021    05002     None     None     None   
47  49622.195601  5.113174e+07  061    45001     None     None     None   

         name                                           geometry  
4       Alloa  MULTIPOLYGON (((-3.81514 56.10242, -3.81924 56...  
11  Aberfoyle  POLYGON ((-4.39592 56.14749, -4.39647 56.14767...  
16     Airlie  POLYGON ((-3.15584 56.65699, -3.15555 56.65681...  
27       Alva  POLYGON ((-3.76332 56.14989, -3.76352 56.14973...  
47        Ayr  POLYGON ((-4.55361 55.42698, -4.55375 55.42697...  


In [27]:
### Finding the dynamic map starting point
'''
steps:
takes first geometric shape
takes everything between the brackets
replace all stray brackets
take first coordinate set
splits into lat and long
'''

starting_pos = str(parish_area['geometry'].iloc[0]) \
                    .split('))')[0].split('((')[1] \
                    .replace('(','').replace(')','') \
                    .split(',')[0] \
                    .split(' ') 

starting_long = starting_pos[1]
starting_lat = starting_pos[0]


In [66]:

### Basic map layer
m = folium.Map(
                location=[starting_long, starting_lat], 
                zoom_start=9,
                tiles='cartodbpositron')

# Set colours location type
marker_colour = {
                'no_sco':'red',
                'has_sco':'blue',
                }


for loc in places.index:
    if not pd.isnull(places['map_loc_latlong'][loc]):
        coord = [float(c) for c in (places['map_loc_latlong'][loc] \
                .replace(",", "") \
                .split(' '))]
        
        loctype = 'no_sco' if pd.isnull(places['place_SCO'].iloc[loc]) else 'has_sco'
        
        folium.Marker(
            location=coord, 
            popup= places['place'][loc]+", "+ loctype,
            tooltip= str(places['place_EN'][loc]) \
                    +", " \
                    +str(places['place_SCO'][loc]),
            #icon=folium.Icon(color=marker_colour[loctype], icon='tint')
            # try this tomorrow
            icon=folium.Icon(color=marker_colour.get(loctype, 'black'), icon='tint')
        ).add_to(m)

### drawing datazone boundaries only
pa_style = {}
folium.GeoJson(parish_area,
                name='parishes',
               style_function=lambda x: {'fillColor': '#ff0000', 
                                         'color': '#ff0000', 
                                         'weight': 1}) \
            .add_to(m)

### Hover over tooltip and geo highlight
map_hover = folium.GeoJson(parish_area,
                    control=False,
                    style_function=lambda x: {'fillColor': '#FFFFFF', 
                                                'color':'#000000', 
                                                'fillOpacity': 0.1, 
                                                'weight': 0.1}, # invisible layer    
                    highlight_function=lambda x: {'fillColor': '#000000', 
                                                    'color':'#000000', 
                                                    'fillOpacity': 0.50, 
                                                    'weight': 0.1}, # style when hovering over                                                                                                
                    tooltip=folium.GeoJsonTooltip(fields=['name'],
                                                    aliases=['Parish'])
)

m.add_child(map_hover)

### Setting layer order and other overheads
m.keep_in_front(map_hover)

folium.LayerControl().add_to(m)

m.save(parent_folder + 'map.html')
m